# LOW CSP Startup Sequence

References:
- [LOW.CSP LMC Documentation](https://developer.skatelescope.org/projects/ska-csp-lmc-low/en/latest/lmc/low_csp_lmc.html)
- [LOW.CSP LMC Tango Clients Examples](https://developer.skatelescope.org/projects/ska-csp-lmc-low/en/latest/example/example.html)
- [CSP LMC commands for AA05](https://confluence.skatelescope.org/display/SE/CSP+LMC+commands+for+AA05)

- Currently the notebook is restricted to testing only a single subarray.

This notebook shows how to transition the LOW CSP from OFFLINE after fresh deployment to ON state. The only deviation noted is that in ON state, the system healthState should report OK (0), currently this is not implemented and the healthState does not update and remains UNKNOWN (3). Since this is a valid failure from expected behavior it is noted as such in the notebook tests, but the user should note that this failure does not affect the fundamental operation of the LOW CSP and can be safely ignored for the moment.

### Viewing Tango attributes

The notebook will interrogate device states and report back attribute values as part of the verification output.    
For visual inspection of device attributes the Taranta API interface is used.    
You can access the interface via a web browser by pointing the URL to the appropriate namespace on your k8s cluster    
`http://<k8s_CLUSTER>/<KUBE_NAMESPACE>/taranta/devices/low-csp/`    
e.g. for a deployment on the CLP    
`http://k8s.clp.skao.int/ska-low-csp-baseline/taranta/devices/low-csp/`

### Prerequisites
- All necessary equipment are installed and verified
- Assume a network is available and all equipment/systems are powered
- P4 switch is configured in order to control CBF
- Fresh deployment of LOW CSP on the k8s cluster

### Imports

In [1]:
import os
import time
from typing import Any

from ska_control_model import AdminMode, ObsState
from tango import Database, DeviceProxy, DevState

### Tango config

This section links the notebook execution to the tango devices on the cluster and requires user updates when the notebook is run on a system other than the Low Digital PSI in Eindhoven.

Ensure the KUBE_NAMESPACE namespace parameter correctly identifies the k8s namespace with which to intend to interact.

In [2]:
# specify here the namespace to connect in this cluster
KUBE_NAMESPACE = "ska-low-csp-baseline"
DATABASEDS_NAME = "ska-low-csp-databaseds"

# finally set the TANGO_HOST
os.environ["TANGO_HOST"] = f"{DATABASEDS_NAME}.{KUBE_NAMESPACE}.svc.cluster.local:10000"

### Tango Database

In [3]:
tango_db = Database()

### Tango proxy devices

In [4]:
# Low Csp controller
csp_ctl_fqdns = tango_db.get_device_exported_for_class("LowCspController").value_string
print("CSP Controllers:")
print(*[" - " + each for each in csp_ctl_fqdns], sep="\n")
csp_controller = DeviceProxy(csp_ctl_fqdns[0])

# Low Csp subarray
csp_subarr_fqdns = tango_db.get_device_exported_for_class("LowCspSubarray").value_string
print("CSP Subarrays:")
print(*[" - " + each for each in csp_subarr_fqdns], sep="\n")
csp_subarray = DeviceProxy(csp_subarr_fqdns[0])

# Cbf controller
cbf_ctl_fqdns = tango_db.get_device_exported_for_class("LowCbfController").value_string
print("CBF Controllers:")
print(*[" - " + each for each in cbf_ctl_fqdns], sep="\n")
cbf_controller = DeviceProxy(cbf_ctl_fqdns[0])

# Cbf Subarray
cbf_subarr_fqdns = tango_db.get_device_exported_for_class("LowCbfSubarray").value_string
print("CBF Subarrays:")
print(*[" - " + each for each in cbf_subarr_fqdns], sep="\n")
cbf_subarray = DeviceProxy(cbf_subarr_fqdns[0])

CSP Controllers:
 - low-csp/control/0
CSP Subarrays:
 - low-csp/subarray/01
 - low-csp/subarray/02
 - low-csp/subarray/03
 - low-csp/subarray/04
CBF Controllers:
 - low-cbf/control/0
CBF Subarrays:
 - low-cbf/subarray/01
 - low-cbf/subarray/02
 - low-cbf/subarray/03
 - low-cbf/subarray/04


In [5]:
csp_devices = (csp_controller, csp_subarray)
cbf_devices = (cbf_controller, cbf_subarray)
all_devices = csp_devices + cbf_devices

### Helper functions

In [6]:
def wait_for_attribute_value(
    device: DeviceProxy,  # pylint: disable = redefined-outer-name
    attribute: str,
    value: Any = True,
    failure_message: str = "Timed out waiting for attribute value",
    timeout_sec: int = 120,
) -> None:
    """
    Wait until an attribute has a certain value.

    :param device: Tango device proxy with the attribute to check
    :param attribute: The name of the attribute
    :param value: Expected value (defaults to True)
    :param failure_message: Message for the exception on failure.
    Defaults to "Timed out waiting for attribute value".
    A note about duration is appended.
    :param timeout_sec: Approximate time-out period  in seconds (in reality
    it could be longer due to delays waiting for each attribute read)
    :raises RuntimeError: if expected value not seen before timing out
    """
    deadline = time.time() + timeout_sec
    poll_interval_seconds = 2
    while time.time() < deadline:
        if device.read_attribute(attribute).value == value:
            break
        time.sleep(poll_interval_seconds)
    else:
        raise RuntimeError(f"{failure_message} after {timeout_sec} sec")


# Coloured printing functions for strings that use universal ANSI escape sequences.
# fail: bold red, pass: bold green


def print_fail(message, start="", end="\n"):
    """Print coloured fail message."""
    print(f"{start}\x1b[1;31m{message}\x1b[0m", end=end)


def print_pass(message, start="", end="\n"):
    """Print coloured pass message."""
    print(f"{start}\x1b[1;32m{message}\x1b[0m", end=end)

### Current state of LOW CSP

**Note**:
if one of the nex assertion FAILED please redeploy your system and run notebook again

In [7]:
assert csp_controller.state() == DevState.DISABLE, "State is not DISABLE"
assert csp_subarray.obsState == ObsState.EMPTY, "LOW CSP Subarray obsState is not EMPTY"
assert csp_controller.adminmode == AdminMode.OFFLINE, "Admin mode of low csp controller is not OFFLINE"
assert str(csp_controller.healthState) == "healthState.UNKNOWN"

assert cbf_controller.state() == DevState.DISABLE, "State is not DISABLE"
assert cbf_subarray.obsState == ObsState.EMPTY, "LOW CBF Subarray obsState is not EMPTY"
assert cbf_controller.adminmode == AdminMode.OFFLINE, "Admin mode of low cbf controller is not OFFLINE"
assert str(csp_controller.healthState) == "healthState.UNKNOWN"

### TMC commands LOW CSP to ONLINE state

In [8]:
for device in all_devices:
    print(f"Initializing TANGO device: {device.name()}")
    device.set_timeout_millis(60_000)
    device.Init()
csp_controller.adminMode = AdminMode.ONLINE
wait_for_attribute_value(csp_controller, "isCommunicating", True)

Initializing TANGO device: low-csp/control/0
Initializing TANGO device: low-csp/subarray/01
Initializing TANGO device: low-cbf/control/0
Initializing TANGO device: low-cbf/subarray/01


## Verify subsystems state after ONLINE command

### LOW CSP devices verification

In [9]:
if csp_controller.state() == DevState.ON:
    print_pass(f"{csp_controller.name()} state is {csp_controller.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_controller.name()} state is {csp_controller.state()}")
    print_fail("Check Failed should be ON")

if csp_subarray.state() == DevState.ON:
    print_pass(f"{csp_subarray.name()} state is {csp_subarray.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_subarray.name()} state is {csp_subarray.state()}")
    print_fail("Check Failed should be ON")

if csp_subarray.obsState == ObsState.EMPTY:
    print_pass(f"{csp_subarray.name()} obsState is {csp_subarray.obsState.value}/{csp_subarray.obsState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_subarray.name()} obsState is {csp_subarray.obsState.value}/{csp_subarray.obsState.name}")
    print_fail("Check Failed should be EMPTY")

if csp_controller.adminmode == AdminMode.ONLINE:
    print_pass(f"{csp_controller.name()} adminmode is {csp_controller.adminmode.value}/{csp_controller.adminmode.name}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_controller.name()} adminmode is {csp_controller.adminmode.value}/{csp_controller.adminmode.name}")
    print_fail("Check Failed should be ONLINE")

if csp_controller.healthState.name == "OK":
    print_pass(f"{csp_controller.name()} healthState is {csp_controller.healthState.value}/{csp_controller.healthState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{csp_controller.name()} healthState is {csp_controller.healthState.value}/{csp_controller.healthState.name}")
    print_fail("Check Failed should be OK")

low-csp/control/0 state is ON
Check passed
low-csp/subarray/01 state is ON
Check passed
low-csp/subarray/01 obsState is 0/EMPTY
Check passed
low-csp/control/0 adminmode is 0/ONLINE
Check passed
low-csp/control/0 healthState is 3/UNKNOWN
Check Failed should be OK


### LOW CBF devices verification

In [10]:
if cbf_controller.state() == DevState.ON:
    print_pass(f"{cbf_controller.name()} state is {cbf_controller.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_controller.name()} state is {cbf_controller.state()}")
    print_fail("Check Failed should be ON")

if cbf_subarray.state() == DevState.ON:
    print_pass(f"{cbf_subarray.name()} state is {cbf_subarray.state()}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_subarray.name()} state is {cbf_subarray.state()}")
    print_fail("Check Failed should be ON")

if cbf_subarray.obsState == ObsState.EMPTY:
    print_pass(f"{cbf_subarray.name()} obsState is {cbf_subarray.obsState.value}/{cbf_subarray.obsState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_subarray.name()} obsState is {cbf_subarray.obsState.value}/{cbf_subarray.obsState.name}")
    print_fail("Check Failed should be EMPTY")

if cbf_controller.adminmode == AdminMode.ONLINE:
    print_pass(f"{cbf_controller.name()} adminmode is {cbf_controller.adminmode.value}/{cbf_controller.adminmode.name}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_controller.name()} adminmode is {cbf_controller.adminmode.value}/{cbf_controller.adminmode.name}")
    print_fail("Check Failed should be ONLINE")

if cbf_controller.healthState.name == "OK":
    print_pass(f"{cbf_controller.name()} healthState is {cbf_controller.healthState.value}/{cbf_controller.healthState.name}")
    print_pass("Check passed")
else:
    print_fail(f"{cbf_controller.name()} healthState is {cbf_controller.healthState.value}/{cbf_controller.healthState.name}")
    print_fail("Check Failed should be OK")

low-cbf/control/0 state is ON
Check passed
low-cbf/subarray/01 state is ON
Check passed
low-cbf/subarray/01 obsState is 0/EMPTY
Check passed
low-cbf/control/0 adminmode is 0/ONLINE
Check passed
low-cbf/control/0 healthState is 3/UNKNOWN
Check Failed should be OK
